<H2>This is Road Event Classification Project for TSML class () Virginia Tech</H2>

Github repo link:

Code modified from: https://github.com/yaorong0921/Driver-Intention-Prediction

Paper link for the inspired architecture: https://arxiv.org/pdf/2006.11557.pdf

In [4]:
#some libraries may need to be installed
#!pip install torch
#!pip install torchvision
import os
import sys
import time
import json
import numpy as np
import torch
from torch import nn
from torch import optim
import pandas as pd
from torch.optim import lr_scheduler
from torch.autograd import Variable
import torchvision
import cv2
from math import log10
import models
import torchvision.transforms.functional as F
import matplotlib.pyplot as plt
from opts import parse_opts
from mean import get_mean, get_std
from spatial_transforms import (
	Compose, Normalize, Scale, CenterCrop, CornerCrop, MultiScaleCornerCrop,
	MultiScaleRandomCrop, RandomHorizontalFlip, ToTensor, DriverFocusCrop, DriverCenterCrop)
from temporal_transforms import LoopPadding, TemporalRandomCrop, TemporalCenterCrop, UniformIntervalCrop
from target_transforms import ClassLabel, VideoID
from target_transforms import Compose as TargetCompose
from models.convolution_lstm import encoder
from utils import AverageMeter, Logger, calculate_accuracy,top_k
from dataset import get_training_set, get_validation_set
import pytorch_ssim
from skimage import filters
import os
os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="0"
os.environ["PYTORCH_CUDA_ALLOC_CONF"]="100"

<h3>This block of code deals with seperating the videos in Brains4Cars dataset into image frames dataset</h3>

In [8]:


import os
from subprocess import check_call
videos = []
paths = []

#empty folder structure for outside image frames dataset
import os

#change inputpath to road camera folder path on your local system
#change outputpath to the folder you would want to store augmented gaze dataset inside
inputpath = 'D:/flownet2_road_camera/'
outputpath = 'D:/outside_frames/'

for dirpath, dirnames, filenames in os.walk(inputpath):
    structure = os.path.join(outputpath, dirpath[len(inputpath):])
    if not os.path.isdir(structure):
        os.mkdir(structure)
    else:
        print("Folder does already exits!")
        
#please change the outside scene path to path in your local system
outside_scene_path=os.path.join('D:'+os.sep,'road_camera')
for path, dirs, files in os.walk(outside_scene_path):
    for f in files:
        if f.endswith('.avi'):
            videos.append(os.path.join(path, f))
            paths.append(path.replace('\\','/'))

for i in range (0,len(videos)):
    filename = videos[i]
    path = paths[i]
    output = os.path.join("D:/outside_frames/"+os.path.basename(path),os.path.basename(filename).split(".")[0],'%6d.png').replace('\\','/')
    #print(os.path.basename(path))
    if(os.path.isdir(os.path.join("D:/outside_frames/"+os.path.basename(path),os.path.basename(filename).split(".")[0]))):
        check_call("ffmpeg -i {0} -f image2 -start_number 0 -vf fps=25 {1}".format(filename,output),shell=True)
        print("ffmpeg -i {0} -f image2 -vf fps=25 {1}".format(filename,output))

Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
F

Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
Folder does already exits!
F

ffmpeg -i D:\road_camera\end_action\20141019_164442_1403_1553.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141019_164442_1403_1553/%6d.png
ffmpeg -i D:\road_camera\end_action\20141019_165104_768_918.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141019_165104_768_918/%6d.png
ffmpeg -i D:\road_camera\end_action\20141019_165800_1773_1923.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141019_165800_1773_1923/%6d.png
ffmpeg -i D:\road_camera\end_action\20141019_170809_486_636.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141019_170809_486_636/%6d.png
ffmpeg -i D:\road_camera\end_action\20141019_170910_222_372.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141019_170910_222_372/%6d.png
ffmpeg -i D:\road_camera\end_action\20141019_171111_1305_1455.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141019_171111_1305_1455/%6d.png
ffmpeg -i D:\road_camera\end_action\20141019_171211_1042_1192.avi -f image2 -vf fps=25 D:/outside_frames/end_act

ffmpeg -i D:\road_camera\end_action\20141115_105550_721_871.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141115_105550_721_871/%6d.png
ffmpeg -i D:\road_camera\end_action\20141115_105650_605_755.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141115_105650_605_755/%6d.png
ffmpeg -i D:\road_camera\end_action\20141115_105851_339_489.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141115_105851_339_489/%6d.png
ffmpeg -i D:\road_camera\end_action\20141115_110323_433_583.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141115_110323_433_583/%6d.png
ffmpeg -i D:\road_camera\end_action\20141115_110825_530_680.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141115_110825_530_680/%6d.png
ffmpeg -i D:\road_camera\end_action\20141115_111027_698_848.avi -f image2 -vf fps=25 D:/outside_frames/end_action/20141115_111027_698_848/%6d.png


KeyboardInterrupt: 

<h3>This block of code is used to generate Gaze Attention Maps</h3>

In [8]:

#empty folder structure for later generation of attention maps
import os

#change inputpath to road camera folder path on your local system
#change outputpath to the folder you would want to store attention maps dataset inside
inputpath = 'D:/flownet2_road_camera/'
outputpath = 'D:/maps/'

for dirpath, dirnames, filenames in os.walk(inputpath):
    structure = os.path.join(outputpath, dirpath[len(inputpath):])
    if not os.path.isdir(structure):
        os.mkdir(structure)
    else:
        print("Folder does already exits!")
        
        
#this block of code is used to generate attention maps in the attention map folder system we generated previously
#this would take a long amount of time to generate
#to skip this step downlad zip from here: 
import os
from subprocess import check_call
videos = []
paths = []
inputpath = 'D:'+os.sep+'maps'+os.sep

for dirpath in os.listdir(inputpath):
    print(dirpath)
    for p in os.listdir(os.path.join(inputpath,dirpath)):
        #print(p)
        structure = os.path.join(inputpath,dirpath,p).replace('\\','/')
        gaze_file_csv_path=os.path.isfile("D:/gaze_results/dgf_video_"+os.path.basename(structure)+"_real.csv")
        if(gaze_file_csv_path):
            df=pd.read_csv(gaze_file_csv_path,header=None)
            #print(df)
            for row in df.iterrows():
                #keep the path of outside video frames dataset here
                attention_map=os.path.join("D:/outside_frames/",dirpath, os.path.basename(structure),'{:06d}.png'.format(int(row[1][0]))).replace('\\','/'))
                if(os.path.isfile(attention_map):
                    raw_image = cv2.imread()
                    #keep the path of attention map dataset here
                    save_path = os.path.join("D:/maps/",dirpath,os.path.basename(structure), '{:06d}.png'.format(row[0])).replace('\\','/')
                    
                    height, width, channels = raw_image.shape
                    
                    print(save_path)
                    sidelen = 300
                    sigma = (sidelen - 1) // 2 // 4
                    blank_image = np.zeros((height,width,3), np.uint8)
                    x=int(row[1][1])
                    y=int(row[1][2])
                    if(int(row[1][1])>=720):
                        x=719
                    if(int(row[1][1])<=0):
                        x=0
                    if(int(row[1][2])>=480):
                        y=479
                    if(int(row[1][2])<=0):
                        y=0
                    blank_image[y,x] = 255
                    #print(blank_image[int(row[1][1]),int(row[1][2])])
                    kernel = filters.gaussian(blank_image, sigma=sigma,multichannel=False)
                    #print(kernel[int(row[1][1]),int(row[1][2])])
                    
                    plt.imsave(save_path,kernel / np.max(kernel))
                 

end_action
D:/maps/end_action/20141019_091035_1106_1256/000000.png
D:/maps/end_action/20141019_091035_1106_1256/000001.png
D:/maps/end_action/20141019_091035_1106_1256/000002.png
D:/maps/end_action/20141019_091035_1106_1256/000003.png
D:/maps/end_action/20141019_091035_1106_1256/000004.png
D:/maps/end_action/20141019_091035_1106_1256/000005.png
D:/maps/end_action/20141019_091035_1106_1256/000006.png
D:/maps/end_action/20141019_091035_1106_1256/000007.png
D:/maps/end_action/20141019_091035_1106_1256/000008.png
D:/maps/end_action/20141019_091035_1106_1256/000009.png
D:/maps/end_action/20141019_091035_1106_1256/000010.png
D:/maps/end_action/20141019_091035_1106_1256/000011.png
D:/maps/end_action/20141019_091035_1106_1256/000012.png
D:/maps/end_action/20141019_091035_1106_1256/000013.png
D:/maps/end_action/20141019_091035_1106_1256/000014.png
D:/maps/end_action/20141019_091035_1106_1256/000015.png
D:/maps/end_action/20141019_091035_1106_1256/000016.png
D:/maps/end_action/20141019_091035_11

D:/maps/end_action/20141019_091136_63_213/000022.png
D:/maps/end_action/20141019_091136_63_213/000023.png
D:/maps/end_action/20141019_091136_63_213/000024.png
D:/maps/end_action/20141019_091136_63_213/000025.png
D:/maps/end_action/20141019_091136_63_213/000026.png
D:/maps/end_action/20141019_091136_63_213/000027.png
D:/maps/end_action/20141019_091136_63_213/000028.png
D:/maps/end_action/20141019_091136_63_213/000029.png
D:/maps/end_action/20141019_091136_63_213/000030.png
D:/maps/end_action/20141019_091136_63_213/000031.png
D:/maps/end_action/20141019_091136_63_213/000032.png
D:/maps/end_action/20141019_091136_63_213/000033.png
D:/maps/end_action/20141019_091136_63_213/000034.png
D:/maps/end_action/20141019_091136_63_213/000035.png
D:/maps/end_action/20141019_091136_63_213/000036.png
D:/maps/end_action/20141019_091136_63_213/000037.png
D:/maps/end_action/20141019_091136_63_213/000038.png
D:/maps/end_action/20141019_091136_63_213/000039.png
D:/maps/end_action/20141019_091136_63_213/0000

D:/maps/end_action/20141019_132535_1548_1698/000048.png
D:/maps/end_action/20141019_132535_1548_1698/000049.png
D:/maps/end_action/20141019_132535_1548_1698/000050.png
D:/maps/end_action/20141019_132535_1548_1698/000051.png
D:/maps/end_action/20141019_132535_1548_1698/000052.png
D:/maps/end_action/20141019_132535_1548_1698/000053.png
D:/maps/end_action/20141019_132535_1548_1698/000054.png
D:/maps/end_action/20141019_132535_1548_1698/000055.png
D:/maps/end_action/20141019_132535_1548_1698/000056.png
D:/maps/end_action/20141019_132535_1548_1698/000057.png
D:/maps/end_action/20141019_132535_1548_1698/000058.png
D:/maps/end_action/20141019_132535_1548_1698/000059.png
D:/maps/end_action/20141019_132535_1548_1698/000060.png
D:/maps/end_action/20141019_132535_1548_1698/000061.png
D:/maps/end_action/20141019_132535_1548_1698/000062.png
D:/maps/end_action/20141019_132535_1548_1698/000063.png
D:/maps/end_action/20141019_132535_1548_1698/000064.png
D:/maps/end_action/20141019_132535_1548_1698/000

D:/maps/end_action/20141019_132726_1056_1206/000069.png
D:/maps/end_action/20141019_132726_1056_1206/000070.png
D:/maps/end_action/20141019_132726_1056_1206/000071.png
D:/maps/end_action/20141019_132726_1056_1206/000072.png
D:/maps/end_action/20141019_132925_1049_1199/000000.png
D:/maps/end_action/20141019_132925_1049_1199/000001.png
D:/maps/end_action/20141019_132925_1049_1199/000002.png
D:/maps/end_action/20141019_132925_1049_1199/000003.png
D:/maps/end_action/20141019_132925_1049_1199/000004.png
D:/maps/end_action/20141019_132925_1049_1199/000005.png
D:/maps/end_action/20141019_132925_1049_1199/000006.png
D:/maps/end_action/20141019_132925_1049_1199/000007.png
D:/maps/end_action/20141019_132925_1049_1199/000008.png
D:/maps/end_action/20141019_132925_1049_1199/000009.png
D:/maps/end_action/20141019_132925_1049_1199/000010.png
D:/maps/end_action/20141019_132925_1049_1199/000011.png
D:/maps/end_action/20141019_132925_1049_1199/000012.png
D:/maps/end_action/20141019_132925_1049_1199/000

D:/maps/end_action/20141019_132925_536_686/000017.png
D:/maps/end_action/20141019_132925_536_686/000018.png
D:/maps/end_action/20141019_132925_536_686/000019.png
D:/maps/end_action/20141019_132925_536_686/000020.png
D:/maps/end_action/20141019_132925_536_686/000021.png
D:/maps/end_action/20141019_132925_536_686/000022.png
D:/maps/end_action/20141019_132925_536_686/000023.png
D:/maps/end_action/20141019_132925_536_686/000024.png
D:/maps/end_action/20141019_132925_536_686/000025.png
D:/maps/end_action/20141019_132925_536_686/000026.png
D:/maps/end_action/20141019_132925_536_686/000027.png
D:/maps/end_action/20141019_132925_536_686/000028.png
D:/maps/end_action/20141019_132925_536_686/000029.png
D:/maps/end_action/20141019_132925_536_686/000030.png
D:/maps/end_action/20141019_132925_536_686/000031.png
D:/maps/end_action/20141019_132925_536_686/000032.png
D:/maps/end_action/20141019_132925_536_686/000033.png
D:/maps/end_action/20141019_132925_536_686/000034.png
D:/maps/end_action/20141019_

...

D:/maps/rturn/20141220_153344_1431_1581/000019.png
D:/maps/rturn/20141220_153344_1431_1581/000020.png
D:/maps/rturn/20141220_153344_1431_1581/000021.png
D:/maps/rturn/20141220_153344_1431_1581/000022.png
D:/maps/rturn/20141220_153344_1431_1581/000023.png
D:/maps/rturn/20141220_153344_1431_1581/000024.png
D:/maps/rturn/20141220_153344_1431_1581/000025.png
D:/maps/rturn/20141220_153344_1431_1581/000026.png
D:/maps/rturn/20141220_153344_1431_1581/000027.png
D:/maps/rturn/20141220_153344_1431_1581/000028.png
D:/maps/rturn/20141220_153344_1431_1581/000029.png
D:/maps/rturn/20141220_153344_1431_1581/000030.png
D:/maps/rturn/20141220_153344_1431_1581/000031.png
D:/maps/rturn/20141220_153344_1431_1581/000032.png
D:/maps/rturn/20141220_153344_1431_1581/000033.png
D:/maps/rturn/20141220_153344_1431_1581/000034.png
D:/maps/rturn/20141220_153344_1431_1581/000035.png
D:/maps/rturn/20141220_153344_1431_1581/000036.png
D:/maps/rturn/20141220_153344_1431_1581/000037.png
D:/maps/rturn/20141220_153344_1

D:/maps/rturn/20141220_153344_59_209/000057.png
D:/maps/rturn/20141220_153344_59_209/000058.png
D:/maps/rturn/20141220_153344_59_209/000059.png
D:/maps/rturn/20141220_153344_59_209/000060.png
D:/maps/rturn/20141220_153344_59_209/000061.png
D:/maps/rturn/20141220_153344_59_209/000062.png
D:/maps/rturn/20141220_153344_59_209/000063.png
D:/maps/rturn/20141220_153344_59_209/000064.png
D:/maps/rturn/20141220_153344_59_209/000065.png
D:/maps/rturn/20141220_153344_59_209/000066.png
D:/maps/rturn/20141220_153344_59_209/000067.png
D:/maps/rturn/20141220_153344_59_209/000068.png
D:/maps/rturn/20141220_153344_59_209/000069.png
D:/maps/rturn/20141220_153344_59_209/000070.png
D:/maps/rturn/20141220_153344_59_209/000071.png
D:/maps/rturn/20141220_153344_59_209/000072.png
D:/maps/rturn/20141220_153344_59_209/000073.png
D:/maps/rturn/20141220_153344_59_209/000074.png
D:/maps/rturn/20141220_153344_59_209/000075.png
D:/maps/rturn/20141220_153344_59_209/000076.png
D:/maps/rturn/20141220_153344_59_209/000

D:/maps/rturn/20141220_153545_159_309/000100.png
D:/maps/rturn/20141220_153545_159_309/000101.png
D:/maps/rturn/20141220_153545_159_309/000102.png
D:/maps/rturn/20141220_153545_159_309/000103.png
D:/maps/rturn/20141220_153545_159_309/000104.png
D:/maps/rturn/20141220_153545_159_309/000105.png
D:/maps/rturn/20141220_153545_159_309/000106.png
D:/maps/rturn/20141220_153545_159_309/000107.png
D:/maps/rturn/20141220_153545_159_309/000108.png
D:/maps/rturn/20141220_153545_159_309/000109.png
D:/maps/rturn/20141220_153545_159_309/000110.png
D:/maps/rturn/20141220_153545_159_309/000111.png
D:/maps/rturn/20141220_153545_159_309/000112.png
D:/maps/rturn/20141220_153545_159_309/000113.png
D:/maps/rturn/20141220_153545_159_309/000114.png
D:/maps/rturn/20141220_153545_159_309/000115.png
D:/maps/rturn/20141220_153545_159_309/000116.png
D:/maps/rturn/20141220_153545_159_309/000117.png
D:/maps/rturn/20141220_153545_159_309/000118.png
D:/maps/rturn/20141220_153545_159_309/000119.png
D:/maps/rturn/201412

D:/maps/rturn/20141220_154451_747_897/000016.png
D:/maps/rturn/20141220_154451_747_897/000017.png
D:/maps/rturn/20141220_154451_747_897/000018.png
D:/maps/rturn/20141220_154451_747_897/000019.png
D:/maps/rturn/20141220_154451_747_897/000020.png
D:/maps/rturn/20141220_154451_747_897/000021.png
D:/maps/rturn/20141220_154451_747_897/000022.png
D:/maps/rturn/20141220_154451_747_897/000023.png
D:/maps/rturn/20141220_154451_747_897/000024.png
D:/maps/rturn/20141220_154451_747_897/000025.png
D:/maps/rturn/20141220_154451_747_897/000026.png
D:/maps/rturn/20141220_154451_747_897/000027.png
D:/maps/rturn/20141220_154451_747_897/000028.png
D:/maps/rturn/20141220_154451_747_897/000029.png
D:/maps/rturn/20141220_154451_747_897/000030.png
D:/maps/rturn/20141220_154451_747_897/000031.png
D:/maps/rturn/20141220_154451_747_897/000032.png
D:/maps/rturn/20141220_154451_747_897/000033.png
D:/maps/rturn/20141220_154451_747_897/000034.png
D:/maps/rturn/20141220_154451_747_897/000035.png
D:/maps/rturn/201412

D:/maps/rturn/20141220_161342_1556_1706/000055.png
D:/maps/rturn/20141220_161342_1556_1706/000056.png
D:/maps/rturn/20141220_161342_1556_1706/000057.png
D:/maps/rturn/20141220_161342_1556_1706/000058.png
D:/maps/rturn/20141220_161342_1556_1706/000059.png
D:/maps/rturn/20141220_161342_1556_1706/000060.png
D:/maps/rturn/20141220_161342_1556_1706/000061.png
D:/maps/rturn/20141220_161342_1556_1706/000062.png
D:/maps/rturn/20141220_161342_1556_1706/000063.png
D:/maps/rturn/20141220_161342_1556_1706/000064.png
D:/maps/rturn/20141220_161342_1556_1706/000065.png
D:/maps/rturn/20141220_161342_1556_1706/000066.png
D:/maps/rturn/20141220_161342_1556_1706/000067.png
D:/maps/rturn/20141220_161342_1556_1706/000068.png
D:/maps/rturn/20141220_161342_1556_1706/000069.png
D:/maps/rturn/20141220_161342_1556_1706/000070.png
D:/maps/rturn/20141220_161342_1556_1706/000071.png
D:/maps/rturn/20141220_161342_1556_1706/000072.png
D:/maps/rturn/20141220_161342_1556_1706/000073.png
D:/maps/rturn/20141220_161342_1

<h3>This code augments attention map to outside scene frames and saves them</h3>

<h4>Used for Early Fusion Network</h4>

In [45]:
#empty folder structure for later generation of augmented gaze dataset
import os

#change inputpath to road camera folder path on your local system
#change outputpath to the folder you would want to store augmented gaze dataset inside
inputpath = 'D:/flownet2_road_camera/'
outputpath = 'D:/aug_gaze_files/'

for dirpath, dirnames, filenames in os.walk(inputpath):
    structure = os.path.join(outputpath, dirpath[len(inputpath):])
    if not os.path.isdir(structure):
        os.mkdir(structure)
    else:
        print("Folder does already exits!")
        
        
#This code augments attention map to outside scene frames and saves them in the augmented gaze dataset folder system which we
#previously generated
import os
from subprocess import check_call
videos = []
paths = []
inputpath = 'D:'+os.sep+'aug_gaze_files'+os.sep

for dirpath in os.listdir(inputpath):
    print(dirpath)
    for p in os.listdir(os.path.join(inputpath,dirpath)):
        #print(p)
        structure = os.path.join(inputpath,dirpath,p).replace('\\','/')
        #print(structure)
        if(os.path.isfile("D:/gaze_results/dgf_video_"+os.path.basename(structure)+"_real.csv")):
            df=pd.read_csv("D:/gaze_results/dgf_video_"+os.path.basename(structure)+"_real.csv",header=None)
            #print(df)
            for row in df.iterrows():
                
                if(os.path.isfile(os.path.join("D:/outside_frames/",dirpath, os.path.basename(structure),'{:06d}.png'.format(int(row[1][0]))).replace('\\','/'))):
                    raw_image = cv2.imread(os.path.join("D:/outside_frames/",dirpath,os.path.basename(structure), '{:06d}.png'.format(int(row[1][0]))).replace('\\','/'))
                    save_path = os.path.join("D:/aug_gaze_files/",dirpath,os.path.basename(structure), '{:06d}.png'.format(row[0])).replace('\\','/')
                    color=cv2.imread(save_path)
                    added_image = cv2.addWeighted(raw_image,0.9,color,0.9,0)
                    plt.imsave(save_path,added_image)
                   

end_action
lchange
lturn
rchange
rturn


<h3>This block of code can be used to generate 5 fold annotation files</h3>

<h4>you could also use the provided annotations from github</h4>

In [ ]:


import random
from glob import glob
from os.path import *
import os
import csv

def N_fold(full_list, n_fold):
    avg = len(full_list) / float(n_fold)
    out = []
    last = 0.0

    while last < len(full_list):
        out.append(full_list[int(last):int(last + avg)])
        last += avg
    return out

data_file_path = 'D:/aug_gaze_files'
file_list = sorted(glob(os.path.join('D:'+os.sep,'aug_gaze_files')+'*/*/*'))
#print(os.path.join('D:'+os.sep,'road_camera'))
random.shuffle(file_list)
#print(join(data_file_path, '*/*/'))
n_fold_list = N_fold(file_list, 5) ## divide into 5 folds
print(file_list)

for i in range (0,5):
    label = []
    subset = []
    n_frames = []
    file_location = []
    for j in range(0,5):
        this_subset = 'training'
        if j == i:
            this_subset = 'validation'
        for file in n_fold_list[j]:
            fbase = file[len(data_file_path):]
            ftarget_idx = fbase.find('/',1)
            ftarget = fbase[1:].split("\\")[0]
            fnum = len(os.listdir(file))
            if(fnum>0):
                file_location.append(fbase[1:])
                n_frames.append(fnum)
                label.append(ftarget)
                subset.append(this_subset)

    with open('D:/Driver-Intention-Prediction/datasets/annotation/fold%d.csv'%i, 'a') as outcsv:   
        #configure writer to write standard csv file
        writer = csv.writer(outcsv, delimiter=',', quotechar='|', quoting=csv.QUOTE_MINIMAL, lineterminator='\n')
        for (w,x,y,z) in zip (file_location,label,n_frames,subset):
            #Write item to outcsv
            writer.writerow([w,x,y,z])

<h2> Baseline Training and Validation </h2>

<h4> please make sure to change: root_path, video_path, annotation_path to appropriate directories before running the code</h4>

In [10]:
import argparse


def parse_opts():
    parser = argparse.ArgumentParser()
    parser.add_argument(
        '--root_path',
        default='D:/Driver-Intention-Prediction',
        type=str,
        help='Root directory path of data')
    parser.add_argument(
        '--video_path',
        default='D:/outside_frames',
        type=str,
        help='Directory path of Videos')
    
    
    parser.add_argument(
        '--annotation_path',
        default='D:/Driver-Intention-Prediction/datasets/annotation',
        type=str,
        help='Annotation file path')
    parser.add_argument(
        '--result_path',
        default='D:/Driver-Intention-Prediction/results',
        type=str,
        help='Result directory path')
    parser.add_argument(
        '--dataset',
        default='Without_gaze',
        type=str,
        help='Used dataset (With_gaze | Without_gaze')
    parser.add_argument(
        '--n_classes',
        default=400,
        type=int,
        help=
        'Number of classes (activitynet: 200, kinetics: 400, ucf101: 101, hmdb51: 51)'
    )
    parser.add_argument(
        '--n_finetune_classes',
        default=5,
        type=int,
        help=
        'Number of classes for fine-tuning. n_classes is set to the number when pretraining.'
    )
    parser.add_argument(
        '--sample_size',
        default=112,
        type=int,
        help='Height and width of inputs')
    parser.add_argument(
        '--sample_duration',
        default=16,
        type=int,
        help='Temporal duration of inputs')
    parser.add_argument(
        '--end_second',
        default=4,
        type=int,
        help='The second before maneuvers. Maximal is 5 seconds, and minimal is 1 second (before maneuvers)')
    parser.add_argument(
        '--interval',
        default=5,
        type=int,
        help='The interval in sampling outside images for training ConvLSTM. From 1 to 30.')
    parser.add_argument(
        '--initial_scale',
        default=1.0,
        type=float,
        help='Initial scale for multiscale cropping')
    parser.add_argument(
        '--n_scales',
        default=3,
        type=int,
        help='Number of scales for multiscale cropping')
    parser.add_argument(
        '--scale_step',
        default=0.84089641525,
        type=float,
        help='Scale step for multiscale cropping')
    parser.add_argument(
        '--train_crop',
        default='corner',
        type=str,
        help=
        'Spatial cropping method in training. random is uniform. corner is selection from 4 corners and 1 center.  (random | corner | center)'
    )
    parser.add_argument(
        '--learning_rate',
        default=0.1,
        type=float,
        help=
        'Initial learning rate (divided by 10 while training by lr scheduler)')
    parser.add_argument('--momentum', default=0.9, type=float, help='Momentum')
    parser.add_argument(
        '--dampening', default=0.9, type=float, help='dampening of SGD')
    parser.add_argument(
        '--weight_decay', default=1e-3, type=float, help='Weight Decay')
    parser.add_argument(
        '--mean_dataset',
        default='kinetics',
        type=str,
        help=
        'dataset for mean values of mean subtraction (activitynet | kinetics)')
    parser.add_argument(
        '--no_mean_norm',
        action='store_true',
        help='If true, inputs are not normalized by mean.')
    parser.set_defaults(no_mean_norm=False)
    parser.add_argument(
        '--std_norm',
        action='store_true',
        help='If true, inputs are normalized by standard deviation.')
    parser.set_defaults(std_norm=False)
    parser.add_argument(
        '--nesterov', action='store_true', help='Nesterov momentum')
    parser.set_defaults(nesterov=False)
    parser.add_argument(
        '--optimizer',
        default='sgd',
        type=str,
        help='Currently only support SGD')

    parser.add_argument(
        '--lr_step',
        default=[30, 60],
        type=list,
        help='Epochs to decay learning rate by 10.'
    )
    parser.add_argument(
        '--batch_size', default=32, type=int, help='Batch Size')
    parser.add_argument(
        '--n_epochs',
        default=50,
        type=int,
        help='Number of total epochs to run')
    parser.add_argument(
        '--begin_epoch',
        default=1,
        type=int,
        help=
        'Training begins at this epoch. Previous trained model indicated by resume_path is loaded.'
    )
    parser.add_argument(
        '--n_val_samples',
        default=1,
        type=int,
        help='Number of validation samples for each activity')
    parser.add_argument(
        '--resume_path',
        default='',
        type=str,
        help='Save data (.pth) of previous training')
    parser.add_argument(
        '--pretrain_path', default='', type=str, help='Pretrained model (.pth)')
    parser.add_argument(
        '--ft_begin_index',
        default=4,
        type=int,
        help='Begin block index of fine-tuning')
    parser.add_argument(
        '--no_train',
        action='store_true',
        help='If true, training is not performed.')
    parser.set_defaults(no_train=False)
    parser.add_argument(
        '--no_val',
        action='store_true',
        help='If true, validation is not performed.')
    parser.set_defaults(no_val=False)

    parser.add_argument(
        '--scale_in_test',
        default=1.0,
        type=float,
        help='Spatial scale in test')
    parser.add_argument(
        '--crop_position_in_test',
        default='c',
        type=str,
        help='Cropping method (c | tl | tr | bl | br) in test')
    parser.add_argument(
        '--no_softmax_in_test',
        action='store_true',
        help='If true, output for each clip is not normalized using softmax.')
    parser.set_defaults(no_softmax_in_test=False)
    parser.add_argument(
        '--no_cuda', action='store_true', help='If true, cuda is not used.')
    parser.set_defaults(no_cuda=False)
    parser.add_argument(
        '--n_threads',
        default=4,
        type=int,
        help='Number of threads for multi-thread loading')
    parser.add_argument(
        '--checkpoint',
        default=5,
        type=int,
        help='Trained model is saved at every this epochs.')
    parser.add_argument(
        '--no_hflip',
        action='store_true',
        help='If true holizontal flipping is not performed.')
    parser.set_defaults(no_hflip=False)
    parser.add_argument(
        '--norm_value',
        default=255,
        type=int,
        help=
        'If 1, range of inputs is [0-255]. If 255, range of inputs is [0-1].')
    parser.add_argument(
        '--model',
        default='resnet',
        type=str,
        help='(resnet | preresnet | wideresnet | resnext | densenet | ')
    parser.add_argument(
        '--model_depth',
        default=18,
        type=int,
        help='Depth of resnet (10 | 18 | 34 | 50 | 101)')
    parser.add_argument(
        '--resnet_shortcut',
        default='A',
        type=str,
        help='Shortcut type of resnet (A | B)')
    parser.add_argument(
        '--wide_resnet_k', default=2, type=int, help='Wide resnet k')
    parser.add_argument(
        '--resnext_cardinality',
        default=32,
        type=int,
        help='ResNeXt cardinality')
    parser.add_argument(
        '--manual_seed', default=1, type=int, help='Manually set random seed')

    parser.add_argument(
        '--n_fold', default=0, type=int, help='the sequence number of the fold (from 0 to 4)')

    args,_ = parser.parse_known_args()


    return args

#import arguments
opt = parse_opts()

#clean cache
import torch
torch.cuda.empty_cache()
#rovides a good alternative for clearing the occupied cuda memory and we can also manually clear the not in use variables by using,

import gc
#del variables
gc.collect()
#start training code




In [ ]:
import os
import sys
import json
import numpy as np
import torch
from torch import nn
from torch import optim
from torch.optim import lr_scheduler

from opts import parse_opts
from model import generate_model
from mean import get_mean, get_std
from spatial_transforms import (
    Compose, Normalize, Scale, CenterCrop, CornerCrop, MultiScaleCornerCrop,
    MultiScaleRandomCrop, RandomHorizontalFlip, ToTensor, DriverFocusCrop, DriverCenterCrop)
from temporal_transforms import LoopPadding, TemporalRandomCrop, TemporalCenterCrop, UniformRandomSample, UniformEndSample
from target_transforms import ClassLabel, VideoID
from target_transforms import Compose as TargetCompose
from dataset import get_training_set, get_validation_set
from utils import Logger

from torch.autograd import Variable
import time
from utils import AverageMeter, calculate_accuracy


if __name__ == '__main__':

    if opt.root_path != '':
        opt.video_path = os.path.join(opt.root_path, opt.video_path)
        opt.annotation_path = os.path.join(opt.root_path, opt.annotation_path)
        opt.result_path = os.path.join(opt.root_path, opt.result_path)
        if opt.resume_path:
            opt.resume_path = os.path.join(opt.root_path, opt.resume_path)
        if opt.pretrain_path:
            opt.pretrain_path = os.path.join(opt.root_path, opt.pretrain_path)
    opt.scales = [opt.initial_scale]
    for i in range(1, opt.n_scales):
        opt.scales.append(opt.scales[-1] * opt.scale_step)
    opt.arch = '{}-{}'.format(opt.model, opt.model_depth)
    opt.mean = get_mean(opt.norm_value, dataset=opt.mean_dataset)
    opt.std = get_std(opt.norm_value)
    print(opt)
    with open(os.path.join(opt.result_path, 'opts.json'), 'w') as opt_file:
        json.dump(vars(opt), opt_file)

    torch.manual_seed(opt.manual_seed)

    torch.cuda.empty_cache()
    gc.collect()
    model, parameters = generate_model(opt)
    print(model)
    #weights = [1, 2, 4, 2, 4]
    #class_weights = torch.FloatTensor(weights).cuda()
    criterion = nn.CrossEntropyLoss()
    if not opt.no_cuda:
        criterion = criterion.cuda()

    if opt.no_mean_norm and not opt.std_norm:
        norm_method = Normalize([0, 0, 0], [1, 1, 1])
    elif not opt.std_norm:
        norm_method = Normalize(opt.mean, [1, 1, 1])
    else:
        norm_method = Normalize(opt.mean, opt.std)

    if not opt.no_train:
        assert opt.train_crop in ['random', 'corner', 'center', 'driver focus']
        if opt.train_crop == 'random':
            crop_method = MultiScaleRandomCrop(opt.scales, opt.sample_size)
        elif opt.train_crop == 'corner':
            crop_method = MultiScaleCornerCrop(opt.scales, opt.sample_size)
        elif opt.train_crop == 'center':
            crop_method = MultiScaleCornerCrop(
                opt.scales, opt.sample_size, crop_positions=['c'])
        elif opt.train_crop == 'driver focus':
            crop_method = DriverFocusCrop(opt.scales, opt.sample_size)
        train_spatial_transform = Compose([
            crop_method,
            MultiScaleRandomCrop(opt.scales, opt.sample_size),
            ToTensor(opt.norm_value), norm_method
        ])
        train_temporal_transform = UniformRandomSample(opt.sample_duration, opt.end_second)
        train_target_transform = ClassLabel()
        train_horizontal_flip = RandomHorizontalFlip()
        training_data = get_training_set(opt, train_spatial_transform,None,
                                         train_temporal_transform, train_target_transform)
        train_loader = torch.utils.data.DataLoader(
            training_data,
            batch_size=opt.batch_size,
            shuffle=True,
            num_workers=opt.n_threads,
            pin_memory=True)
        train_logger = Logger(
            os.path.join(opt.result_path, 'train.log'),
            ['epoch', 'loss', 'acc', 'lr'])
        train_batch_logger = Logger(
            os.path.join(opt.result_path, 'train_batch.log'),
            ['epoch', 'batch', 'iter', 'loss', 'acc', 'lr'])

    if opt.nesterov:
        dampening = 0
    else:
        dampening = opt.dampening
    optimizer = optim.SGD(
        parameters,
        lr=opt.learning_rate,
        momentum=opt.momentum,
        dampening=dampening,
        weight_decay=opt.weight_decay,
        nesterov=opt.nesterov)
    scheduler = lr_scheduler.MultiStepLR(
        optimizer, milestones=opt.lr_step, gamma=0.1)
    if not opt.no_val:
        val_spatial_transform = Compose([
            crop_method,
            MultiScaleRandomCrop(opt.scales, opt.sample_size),
            ToTensor(opt.norm_value), norm_method
        ])
        val_temporal_transform = UniformEndSample(opt.sample_duration, opt.end_second)
        val_target_transform = ClassLabel()
        validation_data = get_validation_set(
            opt, val_spatial_transform, val_temporal_transform, val_target_transform)
        val_loader = torch.utils.data.DataLoader(
            validation_data,
            batch_size=64,
            shuffle=False,
            num_workers=opt.n_threads,
            pin_memory=True)
        val_logger = Logger(
            os.path.join(opt.result_path, 'val.log'), ['epoch', 'loss', 'acc'])

    if opt.resume_path:
        print('loading checkpoint {}'.format(opt.resume_path))
        checkpoint = torch.load(opt.resume_path)
        assert opt.arch == checkpoint['arch']

        opt.begin_epoch = checkpoint['epoch']
        model.load_state_dict(checkpoint['state_dict'])
        if not opt.no_train:
            optimizer.load_state_dict(checkpoint['optimizer'])

    print('run')
    global best_prec
    best_prec = 0
    for epoch in range(opt.begin_epoch, opt.n_epochs + 1):

        if not opt.no_train:
            torch.cuda.empty_cache()
            gc.collect()
            print('train at epoch {}'.format(epoch))

            model.train()

            batch_time = AverageMeter()
            data_time = AverageMeter()
            losses = AverageMeter()
            accuracies = AverageMeter()

            end_time = time.time()
            
            for i, (inputs, targets) in enumerate(train_loader):
                data_time.update(time.time() - end_time)

                if not opt.no_cuda:
                    targets = targets.cuda(non_blocking=True)
                inputs = Variable(inputs)
                targets = Variable(targets)
                outputs = model(inputs)
                loss = criterion(outputs, targets)
                acc = calculate_accuracy(outputs, targets)

                losses.update(loss.item(), inputs.size(0))
                accuracies.update(acc, inputs.size(0))

                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                batch_time.update(time.time() - end_time)
                end_time = time.time()

                train_batch_logger.log({
                    'epoch': epoch,
                    'batch': i + 1,
                    'iter': (epoch - 1) * len(train_loader) + (i + 1),
                    'loss': losses.val,
                    'acc': accuracies.val,
                    'lr': optimizer.param_groups[0]['lr']
                })
                if i % 5 == 0:
                  print('Epoch: [{0}][{1}/{2}]\t'
                      'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                      'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                      'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                      'Acc {acc.val:.3f} ({acc.avg:.3f})'.format(
                          epoch,
                          i + 1,
                          len(train_loader),
                          batch_time=batch_time,
                          data_time=data_time,
                          loss=losses,
                          acc=accuracies))

            train_logger.log({
                'epoch': epoch,
                'loss': losses.avg,
                'acc': accuracies.avg,
                'lr': optimizer.param_groups[0]['lr']
            })

            if epoch % opt.checkpoint == 0:
                save_file_path = os.path.join(opt.result_path,
                                              'save_{}.pth'.format(epoch))
                states = {
                    'epoch': epoch + 1,
                    'arch': opt.arch,
                    'state_dict': model.state_dict(),
                    'optimizer': optimizer.state_dict(),
                }

        #torch.cuda.clear_memory_allocated()
        if not opt.no_val:
            torch.cuda.empty_cache()
            gc.collect()
            print('Validation at epoch {}'.format(epoch))

            model.eval()

            batch_time = AverageMeter()
            data_time = AverageMeter()
            losses = AverageMeter()
            accuracies = AverageMeter()

            end_time = time.time()

            conf_mat = torch.zeros(opt.n_finetune_classes, opt.n_finetune_classes)
            output_file = []
            with torch.no_grad():
                for i, (inputs, targets) in enumerate(val_loader):
                    data_time.update(time.time() - end_time)

                    if not opt.no_cuda:
                        targets = targets.cuda(non_blocking=True)
                    inputs = Variable(inputs, volatile=True)
                    targets = Variable(targets, volatile=True)
                    outputs = model(inputs)
                    loss = criterion(outputs, targets)
                    acc = calculate_accuracy(outputs, targets)
                    

                    ### print out the confusion matrix
                    _,pred = torch.max(outputs,1)
                    for t,p in zip(targets.view(-1), pred.view(-1)):
                        conf_mat[t,p] += 1

                    losses.update(loss.item(), inputs.size(0))
                    accuracies.update(acc, inputs.size(0))

                    batch_time.update(time.time() - end_time)
                    end_time = time.time()

                    print('Epoch: [{0}][{1}/{2}]\t'
                          'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                          'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                          'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                          'Acc {acc.val:.4f} ({acc.avg:.4f})'.format(
                              epoch,
                              i + 1,
                              len(val_loader),
                              batch_time=batch_time,
                              data_time=data_time,
                              loss=losses,
                              acc=accuracies))
                print(conf_mat)

                val_logger.log({'epoch': epoch, 'loss': losses.avg, 'acc': accuracies.avg})

                is_best = accuracies.avg > best_prec
                best_prec = max(accuracies.avg, best_prec)
                print('\n The best prec is %.4f' % best_prec)
                if is_best:
                    states = {
                        'epoch': epoch + 1,
                        'arch': opt.arch,
                        'state_dict': model.state_dict(),
                        'optimizer': optimizer.state_dict(),
                     }
                    save_file_path = os.path.join(opt.result_path,
                                        'baseline_save_best.pth')
                    torch.save(states, save_file_path)

        if not opt.no_train and not opt.no_val:
            scheduler.step()

<h2> Early Fusion Training and Validation </h2>

<h4> please make sure to change: root_path, video_path, annotation_path to appropriate directories before running the code</h4>

In [23]:
import argparse


def parse_opts():
    parser = argparse.ArgumentParser()
    parser.add_argument(
        '--root_path',
        default='D:/Driver-Intention-Prediction',
        type=str,
        help='Root directory path of data')
    parser.add_argument(
        '--video_path',
        default='D:/aug_gaze_files',
        type=str,
        help='Directory path of Videos')
    
    
    parser.add_argument(
        '--annotation_path',
        default='D:/Driver-Intention-Prediction/datasets/annotation',
        type=str,
        help='Annotation file path')
    parser.add_argument(
        '--result_path',
        default='D:/Driver-Intention-Prediction/results',
        type=str,
        help='Result directory path')
    parser.add_argument(
        '--dataset',
        default='Without_gaze',
        type=str,
        help='Used dataset (With_gaze | Without_gaze')
    parser.add_argument(
        '--n_classes',
        default=400,
        type=int,
        help=
        'Number of classes (activitynet: 200, kinetics: 400, ucf101: 101, hmdb51: 51)'
    )
    parser.add_argument(
        '--n_finetune_classes',
        default=5,
        type=int,
        help=
        'Number of classes for fine-tuning. n_classes is set to the number when pretraining.'
    )
    parser.add_argument(
        '--sample_size',
        default=112,
        type=int,
        help='Height and width of inputs')
    parser.add_argument(
        '--sample_duration',
        default=16,
        type=int,
        help='Temporal duration of inputs')
    parser.add_argument(
        '--end_second',
        default=4,
        type=int,
        help='The second before maneuvers. Maximal is 5 seconds, and minimal is 1 second (before maneuvers)')
    parser.add_argument(
        '--interval',
        default=5,
        type=int,
        help='The interval in sampling outside images for training ConvLSTM. From 1 to 30.')
    parser.add_argument(
        '--initial_scale',
        default=1.0,
        type=float,
        help='Initial scale for multiscale cropping')
    parser.add_argument(
        '--n_scales',
        default=3,
        type=int,
        help='Number of scales for multiscale cropping')
    parser.add_argument(
        '--scale_step',
        default=0.84089641525,
        type=float,
        help='Scale step for multiscale cropping')
    parser.add_argument(
        '--train_crop',
        default='corner',
        type=str,
        help=
        'Spatial cropping method in training. random is uniform. corner is selection from 4 corners and 1 center.  (random | corner | center)'
    )
    parser.add_argument(
        '--learning_rate',
        default=0.1,
        type=float,
        help=
        'Initial learning rate (divided by 10 while training by lr scheduler)')
    parser.add_argument('--momentum', default=0.9, type=float, help='Momentum')
    parser.add_argument(
        '--dampening', default=0.9, type=float, help='dampening of SGD')
    parser.add_argument(
        '--weight_decay', default=1e-3, type=float, help='Weight Decay')
    parser.add_argument(
        '--mean_dataset',
        default='kinetics',
        type=str,
        help=
        'dataset for mean values of mean subtraction (activitynet | kinetics)')
    parser.add_argument(
        '--no_mean_norm',
        action='store_true',
        help='If true, inputs are not normalized by mean.')
    parser.set_defaults(no_mean_norm=False)
    parser.add_argument(
        '--std_norm',
        action='store_true',
        help='If true, inputs are normalized by standard deviation.')
    parser.set_defaults(std_norm=False)
    parser.add_argument(
        '--nesterov', action='store_true', help='Nesterov momentum')
    parser.set_defaults(nesterov=False)
    parser.add_argument(
        '--optimizer',
        default='sgd',
        type=str,
        help='Currently only support SGD')

    parser.add_argument(
        '--lr_step',
        default=[30, 60],
        type=list,
        help='Epochs to decay learning rate by 10.'
    )
    parser.add_argument(
        '--batch_size', default=32, type=int, help='Batch Size')
    parser.add_argument(
        '--n_epochs',
        default=50,
        type=int,
        help='Number of total epochs to run')
    parser.add_argument(
        '--begin_epoch',
        default=1,
        type=int,
        help=
        'Training begins at this epoch. Previous trained model indicated by resume_path is loaded.'
    )
    parser.add_argument(
        '--n_val_samples',
        default=1,
        type=int,
        help='Number of validation samples for each activity')
    parser.add_argument(
        '--resume_path',
        default='',
        type=str,
        help='Save data (.pth) of previous training')
    parser.add_argument(
        '--pretrain_path', default='', type=str, help='Pretrained model (.pth)')
    parser.add_argument(
        '--ft_begin_index',
        default=4,
        type=int,
        help='Begin block index of fine-tuning')
    parser.add_argument(
        '--no_train',
        action='store_true',
        help='If true, training is not performed.')
    parser.set_defaults(no_train=False)
    parser.add_argument(
        '--no_val',
        action='store_true',
        help='If true, validation is not performed.')
    parser.set_defaults(no_val=False)

    parser.add_argument(
        '--scale_in_test',
        default=1.0,
        type=float,
        help='Spatial scale in test')
    parser.add_argument(
        '--crop_position_in_test',
        default='c',
        type=str,
        help='Cropping method (c | tl | tr | bl | br) in test')
    parser.add_argument(
        '--no_softmax_in_test',
        action='store_true',
        help='If true, output for each clip is not normalized using softmax.')
    parser.set_defaults(no_softmax_in_test=False)
    parser.add_argument(
        '--no_cuda', action='store_true', help='If true, cuda is not used.')
    parser.set_defaults(no_cuda=False)
    parser.add_argument(
        '--n_threads',
        default=4,
        type=int,
        help='Number of threads for multi-thread loading')
    parser.add_argument(
        '--checkpoint',
        default=5,
        type=int,
        help='Trained model is saved at every this epochs.')
    parser.add_argument(
        '--no_hflip',
        action='store_true',
        help='If true holizontal flipping is not performed.')
    parser.set_defaults(no_hflip=False)
    parser.add_argument(
        '--norm_value',
        default=255,
        type=int,
        help=
        'If 1, range of inputs is [0-255]. If 255, range of inputs is [0-1].')
    parser.add_argument(
        '--model',
        default='resnet',
        type=str,
        help='(resnet | preresnet | wideresnet | resnext | densenet | ')
    parser.add_argument(
        '--model_depth',
        default=18,
        type=int,
        help='Depth of resnet (10 | 18 | 34 | 50 | 101)')
    parser.add_argument(
        '--resnet_shortcut',
        default='A',
        type=str,
        help='Shortcut type of resnet (A | B)')
    parser.add_argument(
        '--wide_resnet_k', default=2, type=int, help='Wide resnet k')
    parser.add_argument(
        '--resnext_cardinality',
        default=32,
        type=int,
        help='ResNeXt cardinality')
    parser.add_argument(
        '--manual_seed', default=1, type=int, help='Manually set random seed')

    parser.add_argument(
        '--n_fold', default=0, type=int, help='the sequence number of the fold (from 0 to 4)')

    args,_ = parser.parse_known_args()


    return args

#import arguments
opt = parse_opts()

#clean cache
import torch
torch.cuda.empty_cache()
#rovides a good alternative for clearing the occupied cuda memory and we can also manually clear the not in use variables by using,

import gc
#del variables
gc.collect()
#start training code




359

In [ ]:
import os
import sys
import json
import numpy as np
import torch
from torch import nn
from torch import optim
from torch.optim import lr_scheduler

from opts import parse_opts
from model import generate_model
from mean import get_mean, get_std
from spatial_transforms import (
    Compose, Normalize, Scale, CenterCrop, CornerCrop, MultiScaleCornerCrop,
    MultiScaleRandomCrop, RandomHorizontalFlip, ToTensor, DriverFocusCrop, DriverCenterCrop)
from temporal_transforms import LoopPadding, TemporalRandomCrop, TemporalCenterCrop, UniformRandomSample, UniformEndSample
from target_transforms import ClassLabel, VideoID
from target_transforms import Compose as TargetCompose
from dataset import get_training_set, get_validation_set
from utils import Logger

from torch.autograd import Variable
import time
from utils import AverageMeter, calculate_accuracy


if __name__ == '__main__':

    if opt.root_path != '':
        opt.video_path = os.path.join(opt.root_path, opt.video_path)
        opt.annotation_path = os.path.join(opt.root_path, opt.annotation_path)
        opt.result_path = os.path.join(opt.root_path, opt.result_path)
        if opt.resume_path:
            opt.resume_path = os.path.join(opt.root_path, opt.resume_path)
        if opt.pretrain_path:
            opt.pretrain_path = os.path.join(opt.root_path, opt.pretrain_path)
    opt.scales = [opt.initial_scale]
    for i in range(1, opt.n_scales):
        opt.scales.append(opt.scales[-1] * opt.scale_step)
    opt.arch = '{}-{}'.format(opt.model, opt.model_depth)
    opt.mean = get_mean(opt.norm_value, dataset=opt.mean_dataset)
    opt.std = get_std(opt.norm_value)
    print(opt)
    with open(os.path.join(opt.result_path, 'opts.json'), 'w') as opt_file:
        json.dump(vars(opt), opt_file)

    torch.manual_seed(opt.manual_seed)

    torch.cuda.empty_cache()
    gc.collect()
    model, parameters = generate_model(opt)
    print(model)
    #weights = [1, 2, 4, 2, 4]
    #class_weights = torch.FloatTensor(weights).cuda()
    criterion = nn.CrossEntropyLoss()
    if not opt.no_cuda:
        criterion = criterion.cuda()

    if opt.no_mean_norm and not opt.std_norm:
        norm_method = Normalize([0, 0, 0], [1, 1, 1])
    elif not opt.std_norm:
        norm_method = Normalize(opt.mean, [1, 1, 1])
    else:
        norm_method = Normalize(opt.mean, opt.std)

    if not opt.no_train:
        assert opt.train_crop in ['random', 'corner', 'center', 'driver focus']
        if opt.train_crop == 'random':
            crop_method = MultiScaleRandomCrop(opt.scales, opt.sample_size)
        elif opt.train_crop == 'corner':
            crop_method = MultiScaleCornerCrop(opt.scales, opt.sample_size)
        elif opt.train_crop == 'center':
            crop_method = MultiScaleCornerCrop(
                opt.scales, opt.sample_size, crop_positions=['c'])
        elif opt.train_crop == 'driver focus':
            crop_method = DriverFocusCrop(opt.scales, opt.sample_size)
        train_spatial_transform = Compose([
            crop_method,
            MultiScaleRandomCrop(opt.scales, opt.sample_size),
            ToTensor(opt.norm_value), norm_method
        ])
        train_temporal_transform = UniformRandomSample(opt.sample_duration, opt.end_second)
        train_target_transform = ClassLabel()
        train_horizontal_flip = RandomHorizontalFlip()
        training_data = get_training_set(opt, train_spatial_transform,None,
                                         train_temporal_transform, train_target_transform)
        train_loader = torch.utils.data.DataLoader(
            training_data,
            batch_size=opt.batch_size,
            shuffle=True,
            num_workers=opt.n_threads,
            pin_memory=True)
        train_logger = Logger(
            os.path.join(opt.result_path, 'train.log'),
            ['epoch', 'loss', 'acc', 'lr'])
        train_batch_logger = Logger(
            os.path.join(opt.result_path, 'train_batch.log'),
            ['epoch', 'batch', 'iter', 'loss', 'acc', 'lr'])

    if opt.nesterov:
        dampening = 0
    else:
        dampening = opt.dampening
    optimizer = optim.SGD(
        parameters,
        lr=opt.learning_rate,
        momentum=opt.momentum,
        dampening=dampening,
        weight_decay=opt.weight_decay,
        nesterov=opt.nesterov)
    scheduler = lr_scheduler.MultiStepLR(
        optimizer, milestones=opt.lr_step, gamma=0.1)
    if not opt.no_val:
        val_spatial_transform = Compose([
            crop_method,
            MultiScaleRandomCrop(opt.scales, opt.sample_size),
            ToTensor(opt.norm_value), norm_method
        ])
        val_temporal_transform = UniformEndSample(opt.sample_duration, opt.end_second)
        val_target_transform = ClassLabel()
        validation_data = get_validation_set(
            opt, val_spatial_transform, val_temporal_transform, val_target_transform)
        val_loader = torch.utils.data.DataLoader(
            validation_data,
            batch_size=64,
            shuffle=False,
            num_workers=opt.n_threads,
            pin_memory=True)
        val_logger = Logger(
            os.path.join(opt.result_path, 'val.log'), ['epoch', 'loss', 'acc'])

    if opt.resume_path:
        print('loading checkpoint {}'.format(opt.resume_path))
        checkpoint = torch.load(opt.resume_path)
        assert opt.arch == checkpoint['arch']

        opt.begin_epoch = checkpoint['epoch']
        model.load_state_dict(checkpoint['state_dict'])
        if not opt.no_train:
            optimizer.load_state_dict(checkpoint['optimizer'])

    print('run')
    global best_prec
    best_prec = 0
    for epoch in range(opt.begin_epoch, opt.n_epochs + 1):

        if not opt.no_train:
            torch.cuda.empty_cache()
            gc.collect()
            print('train at epoch {}'.format(epoch))

            model.train()

            batch_time = AverageMeter()
            data_time = AverageMeter()
            losses = AverageMeter()
            accuracies = AverageMeter()

            end_time = time.time()
            
            for i, (inputs, targets) in enumerate(train_loader):
                data_time.update(time.time() - end_time)

                if not opt.no_cuda:
                    targets = targets.cuda(non_blocking=True)
                inputs = Variable(inputs)
                targets = Variable(targets)
                outputs = model(inputs)
                loss = criterion(outputs, targets)
                acc = calculate_accuracy(outputs, targets)

                losses.update(loss.item(), inputs.size(0))
                accuracies.update(acc, inputs.size(0))

                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                batch_time.update(time.time() - end_time)
                end_time = time.time()

                train_batch_logger.log({
                    'epoch': epoch,
                    'batch': i + 1,
                    'iter': (epoch - 1) * len(train_loader) + (i + 1),
                    'loss': losses.val,
                    'acc': accuracies.val,
                    'lr': optimizer.param_groups[0]['lr']
                })
                if i % 5 == 0:
                  print('Epoch: [{0}][{1}/{2}]\t'
                      'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                      'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                      'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                      'Acc {acc.val:.3f} ({acc.avg:.3f})'.format(
                          epoch,
                          i + 1,
                          len(train_loader),
                          batch_time=batch_time,
                          data_time=data_time,
                          loss=losses,
                          acc=accuracies))

            train_logger.log({
                'epoch': epoch,
                'loss': losses.avg,
                'acc': accuracies.avg,
                'lr': optimizer.param_groups[0]['lr']
            })

            if epoch % opt.checkpoint == 0:
                save_file_path = os.path.join(opt.result_path,
                                              'save_{}.pth'.format(epoch))
                states = {
                    'epoch': epoch + 1,
                    'arch': opt.arch,
                    'state_dict': model.state_dict(),
                    'optimizer': optimizer.state_dict(),
                }

        #torch.cuda.clear_memory_allocated()
        if not opt.no_val:
            torch.cuda.empty_cache()
            gc.collect()
            print('Validation at epoch {}'.format(epoch))

            model.eval()

            batch_time = AverageMeter()
            data_time = AverageMeter()
            losses = AverageMeter()
            accuracies = AverageMeter()

            end_time = time.time()

            conf_mat = torch.zeros(opt.n_finetune_classes, opt.n_finetune_classes)
            output_file = []
            with torch.no_grad():
                for i, (inputs, targets) in enumerate(val_loader):
                    data_time.update(time.time() - end_time)

                    if not opt.no_cuda:
                        targets = targets.cuda(non_blocking=True)
                    inputs = Variable(inputs, volatile=True)
                    targets = Variable(targets, volatile=True)
                    outputs = model(inputs)
                    loss = criterion(outputs, targets)
                    acc = calculate_accuracy(outputs, targets)
                    

                    ### print out the confusion matrix
                    _,pred = torch.max(outputs,1)
                    for t,p in zip(targets.view(-1), pred.view(-1)):
                        conf_mat[t,p] += 1

                    losses.update(loss.item(), inputs.size(0))
                    accuracies.update(acc, inputs.size(0))

                    batch_time.update(time.time() - end_time)
                    end_time = time.time()

                    print('Epoch: [{0}][{1}/{2}]\t'
                          'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                          'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                          'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                          'Acc {acc.val:.4f} ({acc.avg:.4f})'.format(
                              epoch,
                              i + 1,
                              len(val_loader),
                              batch_time=batch_time,
                              data_time=data_time,
                              loss=losses,
                              acc=accuracies))
                print(conf_mat)

                val_logger.log({'epoch': epoch, 'loss': losses.avg, 'acc': accuracies.avg})

                is_best = accuracies.avg > best_prec
                best_prec = max(accuracies.avg, best_prec)
                print('\n The best prec is %.4f' % best_prec)
                if is_best:
                    states = {
                        'epoch': epoch + 1,
                        'arch': opt.arch,
                        'state_dict': model.state_dict(),
                        'optimizer': optimizer.state_dict(),
                     }
                    save_file_path = os.path.join(opt.result_path,
                                        'EF_save_best.pth')
                    torch.save(states, save_file_path)

        if not opt.no_train and not opt.no_val:
            scheduler.step()

In [ ]:
!set'PYTORCH_CUDA_ALLOC_CONF=max_split_size_mb:4000'

<h2> Late Fusion Training and Validation </h2>

<h4> please make sure to change: root_path, video_path, gaze_path, annotation_path to appropriate directories before running the code</h4>

In [17]:
import argparse


def parse_opts():
    parser = argparse.ArgumentParser()
    parser.add_argument(
        '--root_path',
        default='D:/Driver-Intention-Prediction',
        type=str,
        help='Directory path of attention map dataset')
    parser.add_argument(
        '--video_path',
        default='D:/maps',
        type=str,
        help='Directory path of Videos')
    
    parser.add_argument(
        '--gaze_path',
        default='D:/gaze_files',
        type=str,
        help='Directory path of outside frames dataset')
    parser.add_argument(
        '--annotation_path',
        default='D:/Driver-Intention-Prediction/datasets/annotation',
        type=str,
        help='Annotation file path')
    parser.add_argument(
        '--result_path',
        default='D:/Driver-Intention-Prediction/results',
        type=str,
        help='Result directory path')
    parser.add_argument(
        '--dataset',
        default='With_gaze',
        type=str,
        help='Used dataset (With_gaze | Without_gaze')
    parser.add_argument(
        '--n_classes',
        default=400,
        type=int,
        help=
        'Number of classes (activitynet: 200, kinetics: 400, ucf101: 101, hmdb51: 51)'
    )
    parser.add_argument(
        '--n_finetune_classes',
        default=5,
        type=int,
        help=
        'Number of classes for fine-tuning. n_classes is set to the number when pretraining.'
    )
    parser.add_argument(
        '--sample_size',
        default=112,
        type=int,
        help='Height and width of inputs')
    parser.add_argument(
        '--sample_duration',
        default=16,
        type=int,
        help='Temporal duration of inputs')
    parser.add_argument(
        '--end_second',
        default=4,
        type=int,
        help='The second before maneuvers. Maximal is 5 seconds, and minimal is 1 second (before maneuvers)')
    parser.add_argument(
        '--interval',
        default=5,
        type=int,
        help='The interval in sampling outside images for training ConvLSTM. From 1 to 30.')
    parser.add_argument(
        '--initial_scale',
        default=1.0,
        type=float,
        help='Initial scale for multiscale cropping')
    parser.add_argument(
        '--n_scales',
        default=3,
        type=int,
        help='Number of scales for multiscale cropping')
    parser.add_argument(
        '--scale_step',
        default=0.84089641525,
        type=float,
        help='Scale step for multiscale cropping')
    parser.add_argument(
        '--train_crop',
        default='corner',
        type=str,
        help=
        'Spatial cropping method in training. random is uniform. corner is selection from 4 corners and 1 center.  (random | corner | center)'
    )
    parser.add_argument(
        '--learning_rate',
        default=0.1,
        type=float,
        help=
        'Initial learning rate (divided by 10 while training by lr scheduler)')
    parser.add_argument('--momentum', default=0.9, type=float, help='Momentum')
    parser.add_argument(
        '--dampening', default=0.9, type=float, help='dampening of SGD')
    parser.add_argument(
        '--weight_decay', default=1e-3, type=float, help='Weight Decay')
    parser.add_argument(
        '--mean_dataset',
        default='kinetics',
        type=str,
        help=
        'dataset for mean values of mean subtraction (activitynet | kinetics)')
    parser.add_argument(
        '--no_mean_norm',
        action='store_true',
        help='If true, inputs are not normalized by mean.')
    parser.set_defaults(no_mean_norm=False)
    parser.add_argument(
        '--std_norm',
        action='store_true',
        help='If true, inputs are normalized by standard deviation.')
    parser.set_defaults(std_norm=False)
    parser.add_argument(
        '--nesterov', action='store_true', help='Nesterov momentum')
    parser.set_defaults(nesterov=False)
    parser.add_argument(
        '--optimizer',
        default='sgd',
        type=str,
        help='Currently only support SGD')

    parser.add_argument(
        '--lr_step',
        default=[30, 60],
        type=list,
        help='Epochs to decay learning rate by 10.'
    )
    parser.add_argument(
        '--batch_size', default=64, type=int, help='Batch Size')
    parser.add_argument(
        '--n_epochs',
        default=40,
        type=int,
        help='Number of total epochs to run')
    parser.add_argument(
        '--begin_epoch',
        default=1,
        type=int,
        help=
        'Training begins at this epoch. Previous trained model indicated by resume_path is loaded.'
    )
    parser.add_argument(
        '--n_val_samples',
        default=1,
        type=int,
        help='Number of validation samples for each activity')
    parser.add_argument(
        '--resume_path',
        default='',
        type=str,
        help='Save data (.pth) of previous training')
    parser.add_argument(
        '--pretrain_path', default='', type=str, help='Pretrained model (.pth)')
    parser.add_argument(
        '--ft_begin_index',
        default=4,
        type=int,
        help='Begin block index of fine-tuning')
    parser.add_argument(
        '--no_train',
        action='store_true',
        help='If true, training is not performed.')
    parser.set_defaults(no_train=False)
    parser.add_argument(
        '--no_val',
        action='store_true',
        help='If true, validation is not performed.')
    parser.set_defaults(no_val=False)

    parser.add_argument(
        '--scale_in_test',
        default=1.0,
        type=float,
        help='Spatial scale in test')
    parser.add_argument(
        '--crop_position_in_test',
        default='c',
        type=str,
        help='Cropping method (c | tl | tr | bl | br) in test')
    parser.add_argument(
        '--no_softmax_in_test',
        action='store_true',
        help='If true, output for each clip is not normalized using softmax.')
    parser.set_defaults(no_softmax_in_test=False)
    parser.add_argument(
        '--no_cuda', action='store_true', help='If true, cuda is not used.')
    parser.set_defaults(no_cuda=False)
    parser.add_argument(
        '--n_threads',
        default=4,
        type=int,
        help='Number of threads for multi-thread loading')
    parser.add_argument(
        '--checkpoint',
        default=5,
        type=int,
        help='Trained model is saved at every this epochs.')
    parser.add_argument(
        '--no_hflip',
        action='store_true',
        help='If true holizontal flipping is not performed.')
    parser.set_defaults(no_hflip=False)
    parser.add_argument(
        '--norm_value',
        default=255,
        type=int,
        help=
        'If 1, range of inputs is [0-255]. If 255, range of inputs is [0-1].')
    parser.add_argument(
        '--model',
        default='resnet',
        type=str,
        help='(resnet | preresnet | wideresnet | resnext | densenet | ')
    parser.add_argument(
        '--model_depth',
        default=18,
        type=int,
        help='Depth of resnet (10 | 18 | 34 | 50 | 101)')
    parser.add_argument(
        '--resnet_shortcut',
        default='A',
        type=str,
        help='Shortcut type of resnet (A | B)')
    parser.add_argument(
        '--wide_resnet_k', default=2, type=int, help='Wide resnet k')
    parser.add_argument(
        '--resnext_cardinality',
        default=32,
        type=int,
        help='ResNeXt cardinality')
    parser.add_argument(
        '--manual_seed', default=1, type=int, help='Manually set random seed')

    parser.add_argument(
        '--n_fold', default=0, type=int, help='the sequence number of the fold (from 0 to 4)')

    args,_ = parser.parse_known_args()


    return args

#import arguments
opt = parse_opts()

#clean cache
import torch
torch.cuda.empty_cache()
#rovides a good alternative for clearing the occupied cuda memory and we can also manually clear the not in use variables by using,

import gc
#del variables
gc.collect()
#start training code




350

In [ ]:
import os
import gc
import sys
import json
import numpy as np
import torch.utils.data as data
import torch
from torch import nn
from torch import optim
from torch.optim import lr_scheduler

from opts import parse_opts
from model import generate_model
from mean import get_mean, get_std
from spatial_transforms import (
    Compose, Normalize, Scale, CenterCrop, CornerCrop, MultiScaleCornerCrop,
    MultiScaleRandomCrop, RandomHorizontalFlip, ToTensor, DriverFocusCrop, DriverCenterCrop)
from temporal_transforms import LoopPadding, TemporalRandomCrop, TemporalCenterCrop, UniformRandomSample, UniformEndSample
from target_transforms import ClassLabel, VideoID
from target_transforms import Compose as TargetCompose
from dataset import get_training_set, get_validation_set
from utils import Logger

from torch.autograd import Variable
import time
from utils import AverageMeter, calculate_accuracy

from dataset import MyDataset
    
if __name__ == '__main__':

    if opt.root_path != '':
        opt.video_path = os.path.join(opt.root_path, opt.video_path)
        opt.annotation_path = os.path.join(opt.root_path, opt.annotation_path)
        opt.result_path = os.path.join(opt.root_path, opt.result_path)
        if opt.resume_path:
            opt.resume_path = os.path.join(opt.root_path, opt.resume_path)
        if opt.pretrain_path:
            opt.pretrain_path = os.path.join(opt.root_path, opt.pretrain_path)
    opt.scales = [opt.initial_scale]
    for i in range(1, opt.n_scales):
        opt.scales.append(opt.scales[-1] * opt.scale_step)
    opt.arch = '{}-{}'.format(opt.model, opt.model_depth)
    opt.mean = get_mean(opt.norm_value, dataset=opt.mean_dataset)
    opt.std = get_std(opt.norm_value)
    print(opt)
    with open(os.path.join(opt.result_path, 'opts.json'), 'w') as opt_file:
        json.dump(vars(opt), opt_file)

    torch.manual_seed(opt.manual_seed)

    torch.cuda.empty_cache()
    gc.collect()
    model, parameters = generate_model(opt)
    print(model)
    #weights = [1, 2, 4, 2, 4]
    #class_weights = torch.FloatTensor(weights).cuda()
    criterion = nn.CrossEntropyLoss()
    if not opt.no_cuda:
        criterion = criterion.cuda()

    if opt.no_mean_norm and not opt.std_norm:
        norm_method = Normalize([0, 0, 0], [1, 1, 1])
    elif not opt.std_norm:
        norm_method = Normalize(opt.mean, [1, 1, 1])
    else:
        norm_method = Normalize(opt.mean, opt.std)

    if not opt.no_train:
        assert opt.train_crop in ['random', 'corner', 'center', 'driver focus']
        if opt.train_crop == 'random':
            crop_method = MultiScaleRandomCrop(opt.scales, opt.sample_size)
        elif opt.train_crop == 'corner':
            crop_method = MultiScaleCornerCrop(opt.scales, opt.sample_size)
        elif opt.train_crop == 'center':
            crop_method = MultiScaleCornerCrop(
                opt.scales, opt.sample_size, crop_positions=['c'])
        elif opt.train_crop == 'driver focus':
            crop_method = DriverFocusCrop(opt.scales, opt.sample_size)
        train_spatial_transform = Compose([
            crop_method,
            MultiScaleRandomCrop(opt.scales, opt.sample_size),
            ToTensor(opt.norm_value), norm_method
        ])
        train_temporal_transform = UniformRandomSample(opt.sample_duration, opt.end_second)
        train_target_transform = ClassLabel()
        train_horizontal_flip = RandomHorizontalFlip()
        training_data = get_training_set(opt, train_spatial_transform,None,
                                         train_temporal_transform, train_target_transform)
        train_loader = torch.utils.data.DataLoader(
            training_data,
            batch_size=opt.batch_size,
            shuffle=True,
            num_workers=opt.n_threads,
            pin_memory=True)
        
        train_logger = Logger(
            os.path.join(opt.result_path, 'train.log'),
            ['epoch', 'loss', 'acc', 'lr'])
        train_batch_logger = Logger(
            os.path.join(opt.result_path, 'train_batch.log'),
            ['epoch', 'batch', 'iter', 'loss', 'acc', 'lr'])

    if opt.nesterov:
        dampening = 0
    else:
        dampening = opt.dampening
    optimizer = optim.SGD(
        parameters,
        lr=opt.learning_rate,
        momentum=opt.momentum,
        dampening=dampening,
        weight_decay=opt.weight_decay,
        nesterov=opt.nesterov)
    scheduler = lr_scheduler.MultiStepLR(
        optimizer, milestones=opt.lr_step, gamma=0.1)
    if not opt.no_val:
        val_spatial_transform = Compose([
            crop_method,
            MultiScaleRandomCrop(opt.scales, opt.sample_size),
            ToTensor(opt.norm_value), norm_method
        ])
        val_temporal_transform = UniformEndSample(opt.sample_duration, opt.end_second)
        val_target_transform = ClassLabel()
        validation_data = get_validation_set(
            opt, val_spatial_transform, val_temporal_transform, val_target_transform)
       
        val_loader = torch.utils.data.DataLoader(
            validation_data,
            batch_size=64,
            shuffle=False,
            num_workers=opt.n_threads,
            pin_memory=True)
        
        val_logger = Logger(
            os.path.join(opt.result_path, 'val.log'), ['epoch', 'loss', 'acc'])

    if opt.resume_path:
        print('loading checkpoint {}'.format(opt.resume_path))
        checkpoint = torch.load(opt.resume_path)
        assert opt.arch == checkpoint['arch']

        opt.begin_epoch = checkpoint['epoch']
        model.load_state_dict(checkpoint['state_dict'])
        if not opt.no_train:
            optimizer.load_state_dict(checkpoint['optimizer'])

    print('run')
    global best_prec
    best_prec = 0
    for epoch in range(opt.begin_epoch, opt.n_epochs + 1):

        if not opt.no_train:
            torch.cuda.empty_cache()
            gc.collect()
            print('train at epoch {}'.format(epoch))

            model.train()

            batch_time = AverageMeter()
            data_time = AverageMeter()
            losses = AverageMeter()
            accuracies = AverageMeter()

            end_time = time.time()
            
            for i, ((input1,input2),target) in enumerate(train_loader):
                data_time.update(time.time() - end_time)
                if not opt.no_cuda:
                    target = target.cuda(non_blocking=True)
                first_input = Variable(input1)
                second_input = Variable(input2)
                targets = Variable(target)
                #targets = targets.view(opt.batch_size)
                outputs = model((first_input,second_input))
                loss = criterion(outputs, targets)
                acc = calculate_accuracy(outputs, targets)

                losses.update(loss.item(), input1.size(0))
                accuracies.update(acc, input1.size(0))

                optimizer.zero_grad()
                loss.backward()
                optimizer.step()

                batch_time.update(time.time() - end_time)
                end_time = time.time()

                train_batch_logger.log({
                    'epoch': epoch,
                    'batch': i + 1,
                    'iter': (epoch - 1) * len(train_loader) + (i + 1),
                    'loss': losses.val,
                    'acc': accuracies.val,
                    'lr': optimizer.param_groups[0]['lr']
                })
                if i % 5 == 0:
                  print('Epoch: [{0}][{1}/{2}]\t'
                      'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                      'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                      'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                      'Acc {acc.val:.3f} ({acc.avg:.3f})'.format(
                          epoch,
                          i + 1,
                          len(train_loader),
                          batch_time=batch_time,
                          data_time=data_time,
                          loss=losses,
                          acc=accuracies))

            train_logger.log({
                'epoch': epoch,
                'loss': losses.avg,
                'acc': accuracies.avg,
                'lr': optimizer.param_groups[0]['lr']
            })

            if epoch % opt.checkpoint == 0:
                save_file_path = os.path.join(opt.result_path,
                                              'save_{}.pth'.format(epoch))
                states = {
                    'epoch': epoch + 1,
                    'arch': opt.arch,
                    'state_dict': model.state_dict(),
                    'optimizer': optimizer.state_dict(),
                }

        #torch.cuda.clear_memory_allocated()
        if not opt.no_val:
            torch.cuda.empty_cache()
            gc.collect()
            print('Validation at epoch {}'.format(epoch))

            model.eval()

            batch_time = AverageMeter()
            data_time = AverageMeter()
            losses = AverageMeter()
            accuracies = AverageMeter()

            end_time = time.time()

            conf_mat = torch.zeros(opt.n_finetune_classes, opt.n_finetune_classes)
            output_file = []
            with torch.no_grad():
                for i, ((input1,input2),target) in enumerate(val_loader):
                    data_time.update(time.time() - end_time)

                    if not opt.no_cuda:
                        target = target.cuda(non_blocking=True)
                    input1 = Variable(input1, volatile=True)
                    input2 = Variable(input2, volatile=True)
                    targets = Variable(target, volatile=True)
                    outputs = model((input1,input2))
                    #targets = targets.view(opt.batch_size)
                    loss = criterion(outputs, targets)
                    acc = calculate_accuracy(outputs, targets)
                    

                    ### print out the confusion matrix
                    _,pred = torch.max(outputs,1)
                    for t,p in zip(targets.view(-1), pred.view(-1)):
                        conf_mat[t,p] += 1

                    losses.update(loss.item(), input1.size(0))
                    accuracies.update(acc, input1.size(0))

                    batch_time.update(time.time() - end_time)
                    end_time = time.time()

                    print('Epoch: [{0}][{1}/{2}]\t'
                          'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                          'Data {data_time.val:.3f} ({data_time.avg:.3f})\t'
                          'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                          'Acc {acc.val:.4f} ({acc.avg:.4f})'.format(
                              epoch,
                              i + 1,
                              len(val_loader),
                              batch_time=batch_time,
                              data_time=data_time,
                              loss=losses,
                              acc=accuracies))
                print(conf_mat)

                val_logger.log({'epoch': epoch, 'loss': losses.avg, 'acc': accuracies.avg})

                is_best = accuracies.avg > best_prec
                best_prec = max(accuracies.avg, best_prec)
                print('\n The best prec is %.4f' % best_prec)
                if is_best:
                    states = {
                        'epoch': epoch + 1,
                        'arch': opt.arch,
                        'state_dict': model.state_dict(),
                        'optimizer': optimizer.state_dict(),
                     }
                    save_file_path = os.path.join(opt.result_path,
                                        'LF_save_best.pth')
                    torch.save(states, save_file_path)

        if not opt.no_train and not opt.no_val:
            scheduler.step()